In [2]:
import pandas as pd
from matplotlib.figure import Figure

df = pd.read_csv("../src_data/c4-filters.csv")
df

runname  seed  steps  agg_score  \
0    filtering-baseline-2019-18-40gt     5      0   0.330953   
1    filtering-baseline-2019-18-40gt     5   1000   0.357474   
2    filtering-baseline-2019-18-40gt     5   2000   0.377436   
3    filtering-baseline-2019-18-40gt     5   3000   0.387994   
4    filtering-baseline-2019-18-40gt     5   4000   0.396110   
..                               ...   ...    ...        ...   
250                   sm-baseline-c4     6  10000   0.430443   
251                   sm-baseline-c4     6  11000   0.430776   
252                   sm-baseline-c4     6  12000   0.430352   
253                   sm-baseline-c4     6  13000   0.432136   
254                   sm-baseline-c4     6  13500   0.433866   

     commonsense_qa/acc  commonsense_qa/acc_norm  hellaswag/acc  \
0                 0.186                    0.233          0.272   
1                 0.239                    0.271          0.297   
2                 0.280                    0.284          0.321   
3                 0.277                    0.291          0.339   
4                 0.299                    0.315          0.340   
..                  ...                      ...            ...   
250               0.335                    0.326          0.379   
251               0.341                    0.323          0.391   
252               0.340                    0.319          0.392   
253               0.339                    0.326          0.395   
254               0.344                    0.328          0.394   

     hellaswag/acc_norm  openbookqa/acc  openbookqa/acc_norm  ...  siqa/acc  \
0                 0.258           0.166                0.286  ...     0.367   
1                 0.287           0.146                0.260  ...     0.365   
2                 0.332           0.134                0.268  ...     0.368   
3                 0.359           0.132                0.280  ...     0.394   
4                 0.366           0.158                0.286  ...     0.376   
..                  ...             ...                  ...  ...       ...   
250               0.474           0.176                0.340  ...     0.385   
251               0.481           0.192                0.346  ...     0.390   
252               0.475           0.192                0.342  ...     0.377   
253               0.477           0.198                0.348  ...     0.390   
254               0.484           0.198                0.334  ...     0.388   

     siqa/acc_norm  winogrande/acc  winogrande/acc_norm  sciq/acc  \
0            0.362           0.516                0.497     0.210   
1            0.396           0.503                0.486     0.568   
2            0.399           0.519                0.502     0.686   
3            0.404           0.520                0.503     0.721   
4            0.399           0.515                0.500     0.739   
..             ...             ...                  ...       ...   
250          0.406           0.525                0.523     0.767   
251          0.405           0.531                0.515     0.766   
252          0.395           0.528                0.518     0.785   
253          0.405           0.529                0.518     0.785   
254          0.406           0.531                0.523     0.778   

     sciq/acc_norm  arc/acc  arc/acc_norm  mmlu/acc  mmlu/acc_norm  
0            0.202   0.2190        0.2515  0.230285       0.250127  
1            0.502   0.2665        0.2855  0.242526       0.253291  
2            0.590   0.3030        0.3215  0.245745       0.260988  
3            0.622   0.3210        0.3385  0.250427       0.264451  
4            0.620   0.3320        0.3445  0.256134       0.270382  
..             ...      ...           ...       ...            ...  
250          0.675   0.3765        0.3750  0.269139       0.280545  
251          0.676   0.3775        0.3770  0.266895       0.281210  
252          0.688   0.3755        0.3840  0.267159     

In [3]:
pd.unique(df["runname"]).tolist()

['filtering-baseline-2019-18-40gt',
 'filtering-baseline-2019-18-60gt',
 'filtering-c4-all-except-terminal_punct',
 'filtering-c4-all',
 'filtering-c4-curly_bracket',
 'filtering-c4-terminal_punct',
 'filtering-c4-word_lengths',
 'sm-baseline-c4']

In [4]:
runs_mapping = {
 # 'filtering-baseline-2019-18-40gt': "baseline",
 'filtering-baseline-2019-18-60gt': "baseline",
 'filtering-c4-curly_bracket': "curly_bracket filter",
 'filtering-c4-terminal_punct': "terminal_punct filter",
 'filtering-c4-word_lengths': "word_lengths filter",
 'filtering-c4-all': "All filters",
 'filtering-c4-all-except-terminal_punct': "All filters except terminal_punct",
 'sm-baseline-c4': "C4"
}

In [6]:
from matplotlib import pyplot as plt


import json
import os
from matplotlib import pyplot as plt
metrics = ['agg_score', 'commonsense_qa/acc_norm', 'hellaswag/acc_norm', 'openbookqa/acc_norm', 'piqa/acc_norm',
                   'siqa/acc_norm', 'winogrande/acc_norm', 'arc/acc_norm', 'mmlu/acc_norm']

def normalize_runname(runname):
    return runname.replace("/", "_")

grouped = (
    df.groupby(["runname", "steps"])
    .agg(
        {
            key: "mean" for key in metrics
        }
    )
    .reset_index()
)

file_id="../assets/data/plots/c4_filters_hellaswag"
files = {}
for metric in metrics:
    datas = {}
    for name, group in grouped.groupby("runname"):
        if name not in runs_mapping:
            continue
        group = group[["steps", metric]].sort_values(by="steps")
        group = group.set_index("steps")
        rolling_avg = group
        datas[name] = {
            "x": (rolling_avg.index * 2048 * 1024 * 1e-9).tolist(),
            "y": rolling_avg[metric].tolist(),
            "label": runs_mapping[name],
        }
    # Sort the datata based on the steps
    datas = {k: v for k, v in sorted(datas.items(), key=lambda x: -x[1]["y"][-1])}
    # Create a folder
    os.makedirs(f"{file_id}", exist_ok=True)
    with open(f"{file_id}/{normalize_runname(metric)}.json", "w") as f:
        json.dump({
            "data": datas,
            "layout": {
                "title": {
                    "text": "C4 filtering effect on HellaSwag"
                },
            }
        }, f)
    files[metric] = {"file": f"{normalize_runname(metric)}.json"}
# Create index
with open(f"{file_id}/index.json", "w") as f:
    json.dump({
        "files": files,
        "settings": {
            "defaultMetric": "hellaswag/acc_norm",
            "slider":{"min":0,"max":10,"default":3}
        }
    }, f)